In [1]:
import pandas as pd
import os
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import plotly.express as px
import re
import plotly.graph_objects as go
from plotly.subplots import make_subplots
warnings.filterwarnings('ignore')



In [2]:
path="E:\egypt_house_data" # the path of the file

dataframes=[] # our list which i will use to save all the dataframes

for file_name in os.listdir(path): # get all the file names
  real_path=os.path.join(path,file_name) # get the real path we will use to fitch the csv
  df=pd.read_csv(real_path) # read it
  dataframes.append(df) # add it to the list

combined_df = pd.concat(dataframes, ignore_index=True)  # use concat to combine thin in index axis and ignore the index


In [3]:
combined_df.info() # take good look in my dataframe

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 96779 entries, 0 to 96778
Data columns (total 16 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property Size   95641 non-null  object 
 1   Down payment    41913 non-null  object 
 2   Bathrooms       95623 non-null  object 
 3   Property Type   96779 non-null  object 
 4   Available from  8277 non-null   object 
 5   Bedrooms        95597 non-null  object 
 6   Property age    448 non-null    float64
 7   Payment method  93959 non-null  object 
 8   compound        96779 non-null  object 
 9   city            0 non-null      float64
 10  dev             96779 non-null  object 
 11  latitude        96758 non-null  float64
 12  longitude       96758 non-null  float64
 13  description     96779 non-null  object 
 14  url             96779 non-null  object 
 15  price           96779 non-null  object 
dtypes: float64(4), object(12)
memory usage: 11.8+ MB


# first preproccessing our data

### remove duplicate data

In [4]:
combined_df.drop_duplicates(subset=['url'],inplace=True)
combined_df.info()  # wow now we have 7886

<class 'pandas.core.frame.DataFrame'>
Index: 44082 entries, 0 to 96749
Data columns (total 16 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property Size   43582 non-null  object 
 1   Down payment    18557 non-null  object 
 2   Bathrooms       43567 non-null  object 
 3   Property Type   44082 non-null  object 
 4   Available from  4299 non-null   object 
 5   Bedrooms        43547 non-null  object 
 6   Property age    223 non-null    float64
 7   Payment method  42792 non-null  object 
 8   compound        44082 non-null  object 
 9   city            0 non-null      float64
 10  dev             44082 non-null  object 
 11  latitude        44079 non-null  float64
 12  longitude       44079 non-null  float64
 13  description     44082 non-null  object 
 14  url             44082 non-null  object 
 15  price           44082 non-null  object 
dtypes: float64(4), object(12)
memory usage: 5.7+ MB


## convert the columns types to appropriate one

### handle price column

In [5]:
combined_df=combined_df[combined_df["price"] != "unknown"]

In [6]:
combined_df['price'].value_counts()

price
Ask for price     1213
10,000,000 EGP     589
8,000,000 EGP      575
7,000,000 EGP      552
9,000,000 EGP      507
                  ... 
3,915,400 EGP        1
21,710,000 EGP       1
17,110,000 EGP       1
4,301,400 EGP        1
9,875,000 EGP        1
Name: count, Length: 9825, dtype: int64

In [7]:
combined_df=combined_df[ ~((combined_df["price"] == "Ask for price") & (combined_df["Property Size"].isna()))]

In [8]:
combined_df['price'].value_counts()

price
Ask for price     1178
10,000,000 EGP     589
8,000,000 EGP      575
7,000,000 EGP      552
9,000,000 EGP      507
                  ... 
3,915,400 EGP        1
21,710,000 EGP       1
17,110,000 EGP       1
4,301,400 EGP        1
9,875,000 EGP        1
Name: count, Length: 9825, dtype: int64

### Identify and extract the price from descretions for the prices that unknown or ask for price

In [9]:
def extract_real_price(disc):
    patterns = [
        r"سعر\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # pattern 1
        r"price\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # pattern 2
        r"total\s*[price]?\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # pattern 3
    ]
    for pattern in patterns:
        match = re.search(pattern, disc, flags=re.IGNORECASE)
        if match:
            return match.group(1).strip()
    return None

opa=combined_df[combined_df["price"] == "Ask for price"]["description"].apply(extract_real_price,)
opa=opa[opa.notna()]

In [10]:
opa

452                 
600        1 million
630                 
857       27,800,000
891       32,760,000
            ...     
92542     25,000,000
92662    105,000,000
93537     30,000,000
93767      1,155,000
93889               
Name: description, Length: 472, dtype: object

In [11]:
opa.unique()

array(['', '1 million', '27,800,000', '32,760,000', '15,260,468',
       '33,000,000', '29,000,000', '20,900,000', '18,010,000',
       '16,962,000', '45,000,000', '26,416,800', '30,000,000', '307,500',
       '25,183,000', '15,030,000', '38,980,000', '18,310,999',
       '17 million', '24,500,000', '23,000,000', '.',
       '22,000,000   ......', '18000000 MILLION', '20 million',
       '25,737,576', '38,000,000', '800,000', '17,198,000', '57,000,000',
       '21,800,000', '16,000,000', '35,000,000', '50.000.000', '700,000',
       '22,700,000', '15,812,500', '15.000.000', '41,840,000',
       '50,000,000', '29,807,750', '17,105,241', '22,000,0005',
       '43,000,000', '1,500,000', '32,000,000', '29,854,000',
       '18,340,0008', '17,500,000', '22,650,000', '46,250,000',
       '28,000,000', '15,902,000', '20.000.000', '18,127,000',
       '35,988,000', '65,000,000', '26,000,000', '23,146,000',
       '16,332,000',
       '24,000,000..................................................

In [12]:
combined_df.columns

Index(['Property Size', 'Down payment', 'Bathrooms', 'Property Type',
       'Available from', 'Bedrooms', 'Property age', 'Payment method',
       'compound', 'city', 'dev', 'latitude', 'longitude', 'description',
       'url', 'price'],
      dtype='object')

In [13]:

# step 1 we get the values that have million
million_house=opa[opa.str.contains("million", case=False, regex=False)]

# step 2 we apply lambda functions to it to get the values that beside the million
values=million_house.apply(lambda x:x.lower().split('million')[0])

# step 3 convert these values into numberic values
numeric_values=values.str.replace(',','').astype(float)

# step 4 we filter the values  that less than 51 and others that more than 51 to handle the million in each catogery of thim
less_cat=numeric_values[numeric_values <= 51]
more_cat=numeric_values[numeric_values > 51]

print(less_cat.apply(lambda x:x * 1000000))
print(more_cat)

# now as u see in the less one now we handle the million word in the most optimal way

# now we can replace it in our original one
opa[less_cat.index]=less_cat
opa[more_cat.index]=more_cat

600       1000000.0
6083     17000000.0
6997     20000000.0
26812    16000000.0
47969    21000000.0
58562    51000000.0
69969    16000000.0
80576    15000000.0
83263     3000000.0
Name: description, dtype: float64
6795     18000000.0
42584    33250000.0
57112    21500000.0
82224    15000000.0
Name: description, dtype: float64


In [14]:
combined_df.loc[opa.index,"price"]=opa

In [15]:
combined_df["price"].value_counts()["Ask for price"]

np.int64(706)

In [16]:
# ok now after we replace the ask of price as we can we should delete the remaining rows of it
combined_df=combined_df[combined_df["price"] != "Ask for price"]

In [17]:
# now we discover another problem with these values
combined_df=combined_df[~(combined_df["price"]== '')] # ok they are 21 house that we will delete it because we cant get any value from it
combined_df["price"]

0         2,486,400 EGP
1         8,200,000 EGP
2        10,300,000 EGP
3         8,000,000 EGP
4        33,000,000 EGP
              ...      
96700     6,700,000 EGP
96718    23,000,000 EGP
96727    33,000,000 EGP
96735     4,880,000 EGP
96749    18,890,000 EGP
Name: price, Length: 43163, dtype: object

In [18]:
combined_df["price"].value_counts()

price
10,000,000 EGP    589
8,000,000 EGP     575
7,000,000 EGP     552
9,000,000 EGP     507
15,000,000 EGP    482
                 ... 
4,301,400 EGP       1
31,917,000 EGP      1
9,497,000 EGP       1
13,063,000 EGP      1
8,583,000 EGP       1
Name: count, Length: 10041, dtype: int64

### identify and extract the price that written in wrong way in advirsment

In [19]:
def extract_real_price(disc):
    patterns = [
        r"سعر\s*:?\s*([\d.,\s]+(?:\s*(million|thousand|مليون|ألف))?)",  # Arabic price pattern
        r"price\s*:*\s*([\d.,,\s]+(?:\s*(million|thousand))?)",  # English price pattern
        r"total\s*[price]?\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # Total price pattern
        r"asking\s*price\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # Asking price pattern
        r"asking\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # Asking pattern without 'price'
        r"final\s*price\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # Final price pattern
        r"final\s*:?\s*([\d.,\s]+(?:\s*(million|thousand))?)",  # Final pattern without 'price'
        r"asking\s*price\s*:\s*([\d,]+)"  # Specific pattern for 'Asking Price' with comma
    ]
    for pattern in patterns:
        match = re.search(pattern, disc, flags=re.IGNORECASE)
        if match:
            return match.group(1).strip()
    return None

all_patterns = combined_df["description"].apply(extract_real_price)
all_patterns = all_patterns[all_patterns.notna()]

In [20]:
all_patterns[all_patterns.str.contains("million", case=False, regex=False)].unique()

array(['16 Million', '8.000.000  Million', '21,900,000 million',
       '13 million', '49,000,000 million', '62.8 million',
       '9,000,000 million', '26.5 million', '6 million', '1 million',
       '18 Million', '18.2 million', '6.000.000 million',
       '14000000 million', '80 million', '20 million', '10 million',
       '32Million', '15 Million', '95  million', '20 Million',
       '6,350,000 million', '58 million', '28Million', '13.7 million',
       '12,300,000 million', '28.7 million', '27.4 Million',
       '17.3 million', '75 million', '7,500,000 Million', '12 Million',
       '14.7 Million', '55million', '25 Million', '6,326,000 million',
       '14,000,000 million', '47 million', '37 Million',
       '24,000,000 million', '14 million', '17 million', '38 million',
       '4,200,000 million', '10,900 million', '4.6 Million',
       '8.000.000 million', '12000000 million', '7 million', '35 million',
       '23 Million', '100 Million', '6000.000 million', '9 million',
       '

In [21]:
hopa='7.7'
float_hopa=float(hopa)
float_hopa

7.7

In [22]:
# here to handle it we should do more operations in replace
def numeric_replace(disc):
  if len(disc) > 7:
    disc=disc.replace('.','').replace(',','')
  else:
    disc=disc.replace(',','.')
  return disc



# step 1 we get the values that have million
million_house=all_patterns[all_patterns.str.contains("million", case=False, regex=False)]

# step 2 we apply lambda functions to it to get the values that beside the million
values=million_house.str.strip().apply(lambda x:x.lower().split('million')[0])

# step 3 convert these values into numberic values
values=values[values!=''].str.replace(' ','').str.strip().apply(numeric_replace)
print(values.unique())
numeric_values=values.str.replace(',','').astype(float)

# step 4 we filter the values  that less than 51 and others that more than 51 to handle the million in each catogery of thim
less_cat=numeric_values[numeric_values <= 75]
more_cat=numeric_values[numeric_values > 75]

print(less_cat.apply(lambda x:x * 1000000))
print(more_cat)

# now as u see in the less one now we handle the million word in the most optimal way

# now we can replace it in our original one
all_patterns[less_cat.index]=less_cat
all_patterns[more_cat.index]=more_cat

['16' '8000000' '21900000' '13' '49000000' '62.8' '9000000' '26.5' '6' '1'
 '18' '18.2' '6000000' '14000000' '80' '20' '10' '32' '15' '95' '6350000'
 '58' '28' '13.7' '12300000' '28.7' '27.4' '17.3' '75' '7500000' '12'
 '14.7' '55' '25' '6326000' '47' '37' '24000000' '14' '17' '38' '4200000'
 '10.900' '4.6' '12000000' '7' '35' '23' '100' '9' '19' '11' '5.5' '89'
 '85' '10.5' '5789202' '3' '6.6' '27' '23.5' '18000000' '9418000' '30'
 '33' '7850000' '4500' '290000004' '4.4' '7.3' '3900000' '5' '8' '2.5'
 '3586000' '1128000' '59000000' '40' '70' '5000000' '19238260' '13.4'
 '10250000' '8500000' '4300000' '14.5' '13000000' '33250000' '10.9' '26'
 '3.4' '21' '17.9' '6.7' '12.2' '10150000' '16000000' '7427959' '54'
 '20500000' '4' '22000000' '3400000' '4755600' '10300000' '10200000'
 '10900000' '26000000' '31' '7.1' '5.9' '11816099' '3700000' '22500000'
 '45' '69' '13325000' '9.5' '8.700' '7.5' '5.1' '17500000' '5891792' '48'
 '8197000' '31.5' '60' '14350000' '38000000' '22' '17.5' '7000000'

In [23]:
combined_df.loc[all_patterns.index,"price"]

2        10,300,000 EGP
3         8,000,000 EGP
4        33,000,000 EGP
5        16,000,000 EGP
7        16,000,000 EGP
              ...      
96465    12,020,000 EGP
96700     6,700,000 EGP
96718    23,000,000 EGP
96727    33,000,000 EGP
96749    18,890,000 EGP
Name: price, Length: 23651, dtype: object

In [24]:
all_patterns[all_patterns != combined_df.loc[all_patterns.index,"price"].str.replace("EGP","")]

2        10,314,000
3                  
4        33,000,000
5                  
7              16.0
            ...    
96465              
96700     6,700,000
96718    23,000,000
96727    33,000,000
96749    18,890,000
Name: description, Length: 23366, dtype: object

In [25]:
combined_df["price"] = combined_df["price"].str.replace(',','').str.replace('.','').str.replace('EGP', '').str.replace("MILLION","").str.replace("million","").str.replace("3\xa0000000","").str.strip( )

combined_df=combined_df[~(combined_df["price"]== '')]
# Convert the cleaned strings to float
combined_df["price"] =combined_df["price"].astype("float") # now we cleaned our price to make it numerical


In [26]:
combined_df["price"].nlargest(10) # we notice here some problem in price we will handle it in the price per meter column

34869    3.020600e+09
47852    2.500000e+09
51181    1.565000e+09
64020    1.562500e+09
53689    7.000000e+08
14973    6.000000e+08
15239    5.472000e+08
16291    4.000000e+08
84843    4.000000e+08
33882    3.800000e+08
Name: price, dtype: float64

In [27]:
combined_df['url'][33727]

'https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-new-cairo-city-the-5th-settlement-5th-settlement-compounds-the-square-5257669.html'

> **after all processing we do in the price column we still find some wrong numbers we will handle it using the price/met column**

### handle size column

In [28]:
combined_df['size_m']=combined_df['Property Size'].str.split().str[3].str.replace(',', '').str.strip() #
combined_df['size_m']=combined_df['size_m'].astype(float)
combined_df['size_m']

0        148.0
1         95.0
2        173.0
3        183.0
4        228.0
         ...  
96700    160.0
96718    188.0
96727    310.0
96735     99.0
96749    215.0
Name: size_m, Length: 43150, dtype: float64

### create price/met column to use it in analysis

In [29]:
# we create it to make it as unit of measurment we can use against all the groups
combined_df['price/met']=combined_df['price']/combined_df['size_m']
combined_df['price/met']=combined_df['price/met'].round(2)



> **here to avoid any mistakes in size or price we will remove all upnormal price per meter so we make sure that the accuracy of our data is high**



In [30]:
# Filtering rows where 'price/met' is not greater than or equal to 500,000
combined_df = combined_df[combined_df['price/met'] < 500000]

# Filtering rows where 'price/met' is not less than or equal to 10000
combined_df = combined_df[combined_df['price/met'] >= 10000]

In [31]:
combined_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 40159 entries, 0 to 96749
Data columns (total 18 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property Size   40159 non-null  object 
 1   Down payment    18116 non-null  object 
 2   Bathrooms       40150 non-null  object 
 3   Property Type   40159 non-null  object 
 4   Available from  3862 non-null   object 
 5   Bedrooms        40131 non-null  object 
 6   Property age    154 non-null    float64
 7   Payment method  39845 non-null  object 
 8   compound        40159 non-null  object 
 9   city            0 non-null      float64
 10  dev             40159 non-null  object 
 11  latitude        40156 non-null  float64
 12  longitude       40156 non-null  float64
 13  description     40159 non-null  object 
 14  url             40159 non-null  object 
 15  price           40159 non-null  float64
 16  size_m          40159 non-null  float64
 17  price/met       40159 non-null  floa

### analyse the compound column

In [32]:
# combined_df["compound"].str.split(',')[:][1:3]  using that was mistake we should use apply better
combined_df["compound"].str.split(',').head(10)

0    [Verona CompoundCairo,  Mokattam,  Al Hadaba A...
1               [Cali CoastNorth Coast,  Ras Al Hekma]
2    [Palm Hills New CairoCairo,  New Cairo City,  ...
3    [Palm Hills New CairoCairo,  New Cairo City,  ...
4    [MividaCairo,  New Cairo City,  The 5th Settle...
5    [La vista Ras El HikmaNorth Coast,  Ras Al Hekma]
6       [Silver SandsNorth Coast,  Qesm Marsa Matrouh]
7    [Moon ResidencesCairo,  New Cairo City,  The 5...
8       [Silver SandsNorth Coast,  Qesm Marsa Matrouh]
9             [MarassiNorth Coast,  Sidi Abdel Rahman]
Name: compound, dtype: object



> **from here we get the data about how that column written and how we can deal with it to handle it**



In [33]:
# to explore the data in our data we will do that
split_compound=combined_df["compound"].str.split(',',expand=True)
split_compound = split_compound.fillna('Not mentioned')
print(split_compound.shape)
px.treemap(split_compound,path=[0,1,2,3])

(40159, 4)


In [34]:
split_compound[1].unique()

array([' Mokattam', ' Ras Al Hekma', ' New Cairo City',
       ' Qesm Marsa Matrouh', ' Sidi Abdel Rahman', 'Not mentioned',
       ' Sheikh Zayed City', ' 6 October City', ' Hurghada',
       ' Shorouk City', ' Al Ain Al Sokhna', ' New Alamein City',
       ' Mostakbal City - Future City', ' New Capital City',
       ' Al Alamein', ' El Nozha', ' Qesm Ad Dabaah', ' Zamalek',
       ' North Coast Resorts', ' Ring Road', ' Hay Sharq',
       ' New Heliopolis', ' Hay Masr El Kadima',
       ' Heliopolis - Masr El Gedida', ' Ras Sedr', ' Dokki',
       ' Hay El Maadi', ' Obour City', ' Nasr City', ' Mohandessin',
       ' El Khalifa', ' Qesm Borg El Arab', ' Alexandria Compounds',
       ' Hay Torah', ' Marsa Alam', ' Hay Than El Montazah',
       ' Sidi Heneish', ' Sharm El Sheikh',
       ' Cairo Alexandria Desert Road', ' Hay Awal El Montazah',
       ' Markaz Al Hamam', ' Garden City', ' Al Salam City',
       ' Hay Al Amereyah', ' Hay El Haram', ' Badr City',
       ' Hadayek El Ahra

In [35]:
split_compound[split_compound[1] == "Not mentioned"][0].unique()

array(['MadinatyCairo', 'CoronadoNorth Coast', 'HaciendaNorth Coast',
       'Noor CityCairo', 'MohandessinGiza',
       'Heliopolis - Masr El GedidaCairo', 'Sidi Abdel RahmanNorth Coast',
       'North Coast ResortsNorth Coast', 'Ras Al HekmaNorth Coast',
       'Sheikh Zayed CityGiza', 'New Capital CityCairo',
       'Hadayek El AhramGiza', 'New Cairo CityCairo', 'HurghadaRed Sea',
       'FukaNorth Coast', 'Al Ain Al SokhnaSuez', 'Obour CityQalyubia',
       'TantaAl Gharbeya', 'Silver BeachNorth Coast',
       'New Alamein CityNorth Coast', 'Sidi HeneishNorth Coast',
       'Al AlamenMatrouh', 'Garden CityCairo', 'Shorouk CityCairo',
       'Al AlameinNorth Coast', '6 October CityGiza',
       'New Obour CityQalyubia', 'Cairo Alexandria Desert RoadGiza',
       'New HeliopolisCairo', 'New DamiettaDemyat',
       'Ras SedrSouth Sainai', 'Al AgouzaGiza', 'Al AzharCairo',
       'Qesm Marsa MatrouhNorth Coast',
       'Mostakbal City - Future CityCairo', 'ZamalekCairo',
       'Alexan

#### handle the region column more

In [36]:
split_compound.loc[split_compound[split_compound[1] == "Not mentioned"][0].str.split("Cairo|North Coast|Giza|Alexandria|Qalyubia",expand=True)[0].index,1]=split_compound[split_compound[1] == "Not mentioned"][0].str.split("Cairo|North Coast|Giza|Alexandria|Qalyubia",expand=True)[0]
split_compound[1]=split_compound[1].str.strip()
split_compound[1].replace({'New':"New Cairo City"},inplace=True)

In [37]:
split_compound[1].value_counts()

1
New Cairo City                  11495
Ras Al Hekma                     5347
6 October City                   3880
Sheikh Zayed City                3519
Mostakbal City - Future City     2989
                                ...  
Abdeen                              1
Sharm El SheikhSouth Sainai         1
Hay Helwan                          1
New Damietta                        1
Al Menya Al GadeedaAl Menya         1
Name: count, Length: 84, dtype: int64

In [38]:
combined_df["spec_comp"]=split_compound[0]
combined_df["Region"]=split_compound[1]



> **now we have 2 columns one represent the region (bigger area) and the other represent the compound (small area)**



In [39]:
pivot_comp=pd.pivot_table(combined_df, values='price/met', index=['Region'], aggfunc='median')

pivot_comp['house_count']=combined_df.groupby(['Region']).size()


filtered_pivot_comp = pivot_comp[pivot_comp['house_count'] >= 10]
filtered_pivot_comp.nlargest(10,columns='price/met')

price/met  house_count
Region                                     
Sidi Heneish         112608.70           51
Qesm Marsa Matrouh   109090.91         1714
Hacienda             102500.00           95
Qesm Ad Dabaah        95517.65         1275
Sidi Abdel Rahman     95000.00         1687
Ras Al Hekma          93750.00         5347
Mokattam              76524.39          232
North Coast Resorts   72864.66           64
Hurghada              69364.16         1835
New Heliopolis        67608.57          244

In [40]:
combined_df['Region'].unique()

array(['Mokattam', 'Ras Al Hekma', 'New Cairo City', 'Qesm Marsa Matrouh',
       'Sidi Abdel Rahman', 'Madinaty', 'Sheikh Zayed City',
       '6 October City', 'Hurghada', 'Shorouk City', 'Al Ain Al Sokhna',
       'New Alamein City', 'Mostakbal City - Future City',
       'New Capital City', 'Al Alamein', 'El Nozha', 'Qesm Ad Dabaah',
       'Zamalek', 'North Coast Resorts', 'Ring Road', 'Hay Sharq',
       'New Heliopolis', 'Coronado', 'Hay Masr El Kadima', 'Hacienda',
       'Heliopolis - Masr El Gedida', 'Ras Sedr', 'Dokki', 'Hay El Maadi',
       'Obour City', 'Nasr City', 'Mohandessin', 'El Khalifa',
       'Qesm Borg El Arab', 'Noor City', 'Alexandria Compounds',
       'Hay Torah', 'Marsa Alam', 'Hay Than El Montazah', 'Sidi Heneish',
       'Sharm El Sheikh', 'Cairo Alexandria Desert Road', '',
       'Hay Awal El Montazah', 'Markaz Al Hamam', 'Hadayek El Ahram',
       'Garden City', 'HurghadaRed Sea', 'Fuka', 'Al Ain Al SokhnaSuez',
       'TantaAl Gharbeya', 'Al Salam City

In [41]:
combined_df.loc[combined_df['spec_comp'] == 'North Coast ResortsNorth Coast', 'Region'] = 'North Coast Resorts'

In [42]:
combined_df[combined_df['Region'] == '']

Property Size Down payment Bathrooms Property Type  \
47693  1,808 sqft / 168 sqm  675,400 EGP         3     Apartment   
83207  2,476 sqft / 230 sqm          NaN         3     Apartment   

      Available from Bedrooms  Property age         Payment method  \
47693            NaN       4            NaN  Cash or  Installments   
83207     3 Apr 2024       3            NaN                   Cash   

                               compound  city  \
47693  Cairo Alexandria Desert RoadGiza   NaN   
83207    Alexandria CompoundsAlexandria   NaN   

                                             dev  latitude  longitude  \
47693  Swanda island real estate(111 Properties)  31.15126   30.00380   
83207   Coldwell Banker Platinum(245 Properties)  29.92444   31.20174   

                                             description  \
47693  شقة للبيع فى كمبوند ميدجارد احدى كمبوندات مجمو...   
83207  -Apartment for sale, 230m, Smouha (Valory Anto...   

                                                     url      price  size_m  \
47693  https://www.propertyfinder.eg/en/plp/buy/apart...  4052400.0   168.0   
83207  https://www.propertyfinder.eg/en/plp/buy/apart...  5500000.0   230.0   

       price/met                         spec_comp Region  
47693   24121.43  Cairo Alexandria Desert RoadGiza         
83207   23913.04    Alexandria CompoundsAlexandria

### available from

In [43]:
combined_df["Available from"].value_counts()


Available from
15 May 2024    196
14 May 2024    174
12 May 2024    165
21 May 2024    159
11 May 2024    152
              ... 
29 Aug 2023      1
15 Jan 2024      1
19 Dec 2023      1
20 Mar 2025      1
20 Jun 2023      1
Name: count, Length: 314, dtype: int64

In [44]:
# lets discover the url of thim
avail_df=combined_df[combined_df["Available from"].notnull()]
avail_df['Available from'] = pd.to_datetime(avail_df['Available from'], format="%d %b %Y")


In [45]:
avail_df['Available from']

1       2024-05-15
4       2024-05-08
5       2024-05-14
16      2024-04-25
17      2024-05-15
           ...    
94059   2024-01-31
94067   2024-04-28
95879   2024-05-20
96727   2024-04-30
96735   2024-04-28
Name: Available from, Length: 3862, dtype: datetime64[ns]

In [46]:
px.scatter(avail_df,x="size_m",y="Available from") # i think there is no relation ship or any value we can take from here
# i tried price
# size
# Down payment and nothing

### Property age

In [47]:
age_df=combined_df[combined_df["Property age"].notnull()]


In [48]:
px.scatter(age_df,x="Property age",y="price") # it doesnt have that enough value

### Down payment



> **first here we are trying to fill the nulls in your down payment column by discovering the description and try to get from it the down payment of houses we couldn't take it in web scraping**



In [49]:
# we will try to increase the Down payment column from the descreption

#lets try to take random houses that have down payment with null
down_df=combined_df[combined_df["Down payment"].isnull()]



> **This operation required several hours of effort to develop and refine effective patterns
 that accurately extract the complete down payment information from descriptions.**







In [50]:
down_df["description"][2]

'Project Name: Palm Hills New Cairo Developer Name: Palm HillsUnit Type: Apartment Ground Floor BUA: 172 SQMGarden: 66 SQM3 Bedrooms3 BathroomsReady To MoveVery Prime Location Down Payment: 7,000,000 EGPTotal Price: 10,314,000 EGPRemaining of installments: 3,313,950 EGP till 2033 93,000 EGP Per Quarter  Buyer Commission: 1,5%======================================Palm Hills Developments was established in 2005, and is one of the leading real estate companies.The history of Palm Hills stretches decades of experience in real estate development. The company has implemented many successful projects. The company is known for providing luxurious and modern projects that exceed customer expectations.Palm Hills focuses on developing residential, commercial and entertainment real estate. It works to create integrated communities that enhance modern lifestyle and meet the needs of both residents and investors. The company always looks to realize its vision of providing high quality projects that 

In [51]:
def extract_down_pay(description):
    patterns = [
        r"([\d.,٬٫\s]+\%*)\s*down\s*payment\s*(?!:)",  # pattern 1
        r"with\s*a?\s*(\d+\s*%*)\s*down\s*payment",  # pattern 2
        r"Down Payments?\s*\:*\s*([\d.,٬٫\s]+\%*\s*(million|thousand|EGP)?)",  # pattern 3
        r"ب?مقدم\s*:?([\d.,٬٫\s]+)",  # pattern 4
        r"down\s*payments?\s*of\s*\(*\)*\:*\“*\=*([\d.,٬٫\s]*\s*\w{5,8})\“*", # pattern 5
        r"DP\s*\:*([\d.,٬٫\s]*\%*)",
        r"(\d+\s*\%?)\s*is\s*required" # pattern 6
    ]

    for pattern in patterns:
        match = re.search(pattern, description, flags=re.IGNORECASE)
        if match:
            return match.group(1)
    return None
all_pattern=down_df["description"].apply(extract_down_pay)
all_pattern[all_pattern.notnull()] # now i get from here 6535 house lets try to get more

2                                            7,000,000 EGP
6                                                         
8        40.00.000........................................
10                                                        
16                                                        
                               ...                        
94428                                            8,370,000
94434                                                     
95739                                            8,370,000
95765                                            5,070,000
96677                                            3,821,000
Name: description, Length: 8901, dtype: object


>**after we get the data as we want we find a lot of conditions we should handle like empty spaces , single number not all of it and word not a number that what we will try to handle here**



In [52]:
all_pattern[all_pattern == " "] # there are 4740 one with empty space we will try to handle it with functions as we can

6         
10        
16        
99        
101       
        ..
93992     
93995     
94010     
94100     
94434     
Name: description, Length: 2229, dtype: object

In [53]:
all_patten=all_pattern[all_pattern.notnull()]



> **now here at this point we have alot of indexes that we are sure they have down payment but for some reason in regex (which this the best thing i can get) some of thim get an empty space we will use that function to handle that**



#### handle the descreptions that have multiple down payment phrases to get the right one

In [54]:
# the function that handles the mistakes in regex
def handle_empty_space(disc):
    return re.split('Down Payment', disc, flags=re.IGNORECASE)

ok=down_df[all_pattern == " "]["description"].apply(handle_empty_space)

In [55]:
print(ok)

6        [Resale chalet in Silversand with the lowest ,...
10       [فيلا للبيع بمدينتي ناصية نموذج F3 Town House ...
16       [Limitted Offer Villa DoubleView Zero Downpaym...
99       [Property Details:Very Prime Location Apartmen...
101      [Finished Chalet in Ras El Hikma North CoastVi...
                               ...                        
93992    [Own a 370-meter twin house in the most presti...
93995    [✅ Project name: Sephora Heights New Cairo.✔️ ...
94010    [Marassem Fifth square New cairoOpen view land...
94100    [VERY HOT DEAL for investors & end users mount...
94434    [Apartment 100 sqmVery special viewIn Crest Co...
Name: description, Length: 2229, dtype: object


In [56]:
ok_1_2=ok.apply(lambda x:x if len(x) == 2 else None ).dropna() # after we split every value in the Down payment some of thim have multiple down payment words
# so we include first the ones which has only one down payment phrase
print(ok_1_2)

99       [Property Details:Very Prime Location Apartmen...
101      [Finished Chalet in Ras El Hikma North CoastVi...
108      [For sale at the cheapest price in Mostakbal C...
120      [Project Name: EtapaDeveloper Name: City EdgeU...
126      [Ad ID: 870 ========Brand new apartment direct...
                               ...                        
93796    [inished and furnished cabin on the northern c...
93813    [Lake View Residence 2Type: Apartment - BUA: 1...
93867    [Penthouse chalet for sale in La Vista Ain Sok...
93995    [✅ Project name: Sephora Heights New Cairo.✔️ ...
94434    [Apartment 100 sqmVery special viewIn Crest Co...
Name: description, Length: 1810, dtype: object


In [57]:
def extract_number_1(disc):
    match = re.search(r"\:*\s*([\d.٫,%]+\s*(thousand|million)?)(?!years)", disc,flags=re.IGNORECASE)
    return match.group(1) if match else None


ok_1=ok_1_2.apply(lambda x:x[1])
# here we make the regex specific for those to get the values from it

down_emp=ok_1.apply(extract_number_1) # now as we see we get alot of numbers but we should filter it also
down_emp

99        3,954,784 
101        1,503,000
108             10% 
120      12,000,000 
126               , 
            ...     
93796     2,100,000 
93813     3,915,400 
93867      3 million
93995           15% 
94434              7
Name: description, Length: 1810, dtype: object

In [58]:
# now for my view every 2 numbers only may be get the wrong number that what we will try to do now
down_emp_wrong_num=down_emp[down_emp.notnull()].apply(lambda x: x if len(x) < 2 else None).dropna() # now we will try to handle thim if we can
down_emp_wrong_num

137      6
238      6
522      6
539      9
876      6
        ..
82648    .
82727    4
83069    5
89228    8
94434    7
Name: description, Length: 135, dtype: object

In [59]:
# here we are trying to handle the wrongs in our handles function
def extract_number_0(disc):
   return disc[len(disc) - 15:len(disc)]

wrong_number=ok_1_2.loc[down_emp_wrong_num.index]
wrong_number_0=wrong_number.apply(lambda x:x[0])
wrong_number_0=wrong_number_0.apply(extract_number_0)
wrong_number_0

137      stems:-Without 
238      stems:-Without 
522      stems:-Without 
539      ith the lowest 
876       3,000,000 egp 
              ...       
82648    vices: limited 
82727    ort 13,000,000 
83069    ,000For 8 years
89228    ith the lowest 
94434    ith the lowest 
Name: description, Length: 135, dtype: object

In [60]:
def handle_words(disc):
    li = ["the lowest", "without", "ZERO"]
    for word in li:
        if isinstance(disc, str) and re.search(word, disc, flags=re.IGNORECASE):
            return 0
    return disc

# Convert to string type
wrong_number_0 = wrong_number_0.astype(str)

# Apply the function to the Series
wrong_number_0 = wrong_number_0.apply(handle_words)

print(wrong_number_0)

137                    0
238                    0
522                    0
539                    0
876       3,000,000 egp 
              ...       
82648    vices: limited 
82727    ort 13,000,000 
83069    ,000For 8 years
89228                  0
94434                  0
Name: description, Length: 135, dtype: object


In [61]:
# so now we will start to handle all that and put it in our data frame
# first we will put the 277 one in the bigger 1 to have thim all in one place
down_emp.update(wrong_number_0) # ok now we have all of the 4031 here now we will update it in the bigger one
all_patten.update(down_emp)

#### handle all the conditions we nead to reach the correct downpayment number

In [62]:
# lets first add it to the column then we will handle all the strings there
combined_df["Down payment"].update(all_patten)

In [63]:
# after we finished all that the returned have some text like million thousand and others that should be handles that what we did in that cell
def handle_percentage(row):
  match=re.search(r"(\d+)%",row["Down payment"])
  if match:
    return float(match.group(1))/100 * row["price"]
  else:
    return 0
def handle_remain_arab(row):
    # Use a character class to match either "ي" or "ى"
    match = re.search(r"(\d+)\s*متبق[يى]", row["Down payment"])
    if match:
        return row["price"] - float(match.group(1))
    else:
        return 0

def handle_words_not_num(disc):
    if isinstance(disc, str) and disc.isnumeric():
        return disc
    return None

combined_df["Down payment"] = (
    combined_df["Down payment"]
    .str.replace("EGP", "")
    .str.replace(",", "")
    .str.replace(" ", "")
    .str.replace(".", "")
    .str.replace("Notrequired", "0")
    .str.replace("و", "")
    .str.replace("million","000000")
    .str.replace("thousand","000")
    .str.replace("Egp","")
    .str.replace("٫","")
    .str.replace("y","")
    .str.replace("LE","")
    .str.replace("ort","")
    .str.replace("egp","")
    .str.replace("ns","")
    .str.replace("٬","")

)
combined_df["Down payment"]=combined_df[combined_df["Down payment"].notnull()]["Down payment"]

handle_percentage=combined_df[combined_df["Down payment"].str.contains('%',na=False)].apply(handle_percentage,axis=1)
combined_df.loc[handle_percentage.index,"Down payment"]=handle_percentage

handle_remain=combined_df[combined_df["Down payment"].str.contains("متبقى",na=False)].apply(handle_remain_arab,axis=1)
combined_df.loc[handle_remain.index,"Down payment"]=handle_remain

handle_words=combined_df["Down payment"].apply(handle_words_not_num)
combined_df.loc[handle_words.index,"Down payment"]=handle_words

handle_remain_1=combined_df[combined_df["Down payment"].str.contains("متبقي",na=False)].apply(handle_remain_arab,axis=1)
combined_df.loc[handle_remain_1.index,"Down payment"]=handle_remain_1

combined_df["Down payment"]=combined_df["Down payment"].astype(float) # now there is alot to handle here

In [64]:
combined_df["Down payment"].notnull().sum() # now the last thing we make it from 18000 to 23000 so then our statics will be more accurate

np.int64(23331)

In [65]:
combined_df["Down payment"].fillna(-1,inplace=True) # we will make it -1 to refer its cash not in installment

In [66]:
combined_df["Down payment"].value_counts() # alot of -1 that we couldnt get the value of it

Down payment
-1.0           16828
 0.0            1190
 1000000.0       361
 2000000.0       332
 1500000.0       298
               ...  
 3205532.0         1
 10598000.0        1
 1783000.0         1
 6852200.0         1
 4379532.0         1
Name: count, Length: 6962, dtype: int64

In [67]:
# Create the scatter plot with Plotly Express
fig = px.scatter(combined_df, x="Down payment", y="price",color="Property Type")
print(len(combined_df))
# Set y-axis limit to 50 million (50,000,000)
fig.update_yaxes(range=[0, 25000000])
fig.update_xaxes(range=[0, 25000000])
# Customize the plot layout (optional)
fig.update_layout(
    title="Scatter Plot of Down Payment vs. Pricepermeter",
    xaxis_title="Down Payment",
    yaxis_title="Price"
)

# Show the plot
fig.show()

# ok we will make functions with this column until we get it

40159


### find the years of installments

In [68]:
# ok now we will make the duration of installment column so we can use it later
instal_df=combined_df[~(combined_df["Down payment"] == -1)]
instal_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 23331 entries, 0 to 96749
Data columns (total 20 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property Size   23331 non-null  object 
 1   Down payment    23331 non-null  float64
 2   Bathrooms       23329 non-null  object 
 3   Property Type   23331 non-null  object 
 4   Available from  1876 non-null   object 
 5   Bedrooms        23328 non-null  object 
 6   Property age    70 non-null     float64
 7   Payment method  23253 non-null  object 
 8   compound        23331 non-null  object 
 9   city            0 non-null      float64
 10  dev             23331 non-null  object 
 11  latitude        23329 non-null  float64
 12  longitude       23329 non-null  float64
 13  description     23331 non-null  object 
 14  url             23331 non-null  object 
 15  price           23331 non-null  float64
 16  size_m          23331 non-null  float64
 17  price/met       23331 non-null  floa

In [69]:
def extract_years_installment(disc):
    # Combine multiple Arabic and English patterns using the | operator
    patterns = [
        r"حت[يى]?\s+\w+\s+(\d+\s*\w?)", # pattern 1
        r"installments?\s*:?\s*(\d+\s*\w?)", # pattern 2
        r"(\d+\s*\w?)\s*\w+\s*InstallmentDelivery", # pattern 4
        r"(\d+\s*\w?)\s*\w+\s*installments?", # pattern 5
        r"تصل\s+الي\s+(\d+\s*\w?)\s+", # pattern 6
        r"[أا]قساط\s+على\s+(\d+\s*\w?)",# pattern 7
        r"Installments?\s*up\s*to\s*(\d+\s*\w?)", # pattern 8
        r"قسط\s+ل\s+(\d+\s*\w?)", # pattern 9
        r"installments?\s*for\s*(\d+\s*\w?)", # pattern 10
        r"installments?\s*till\s*\w*\s*(\d+\s*\w?)",# pattern 11
        r"installments?\s*Delivery\s*\:*(\d+\s*\w?)",
        r"over\s*(\d+\s*\w?)", # pattern 12


    ]

    for pattern in patterns:
        match = re.search(pattern, disc, flags=re.IGNORECASE)
        if match:
            return match.group(1)
    return None

all_patterns=instal_df["description"].apply(extract_years_installment)
ins_al=all_patterns[all_patterns.notna()]



> **i tried in the code to add the year month , سنة and سنين but it gives me only 3000 instead of 15000 so i choose this hard way**



In [70]:
ins_al

1          8 y
2            3
5          6 y
11        12 Y
12         8 y
         ...  
96642      8 y
96677     000E
96700       00
96718    485 a
96749    000 E
Name: description, Length: 13358, dtype: object

In [71]:
combined_df["description"][65838]

'Villa for sale in Hyde Park with open viewBuildings 327 metersLand 427 metersView Landscapeprice: 28,000,000About the Hyde Park project: An integrated residential complex located near the ring road on the main 90th Street. Location of Hyde Park Compound, Fifth Settlement: in the heart of Fifth Settlement in New Cairo. Hyde Park area: 1,200 acres, or approximately 5 million square meters. Unit types: Hyde Park Fifth Settlement apartments - duplex - twin houses - townhouses Hyde Park Fifth Settlement - villa for sale Hyde Park Fifth Settlement - commercial storesUnits area: starts from 99 square meters and reaches 677 square meters_______'

In [72]:

# ok now lets discover what is onther patterns we can add
instal_df[all_patterns.isnull()].sample(10)

Property Size  Down payment Bathrooms Property Type  \
49026   2,185 sqft / 203 sqm     4300000.0         4     Apartment   
41050   1,345 sqft / 125 sqm     7526400.0         3     Apartment   
51398   2,626 sqft / 244 sqm     8527416.0       3.0    Twin House   
37020   1,496 sqft / 139 sqm     2140000.0         2     Apartment   
13580   2,260 sqft / 210 sqm    25000000.0         3     Apartment   
17443   1,722 sqft / 160 sqm     1570000.0         3        Chalet   
17275   2,691 sqft / 250 sqm      600000.0         3     Penthouse   
1335    2,336 sqft / 217 sqm     5800000.0         4         Villa   
45620   2,282 sqft / 212 sqm     2600000.0       3.0     Townhouse   
1711    1,324 sqft / 123 sqm           0.0         2     Apartment   

      Available from   Bedrooms  Property age         Payment method  \
49026            NaN  5  + Maid           NaN  Cash or  Installments   
41050            NaN          3           NaN                   Cash   
51398            NaN        3.0           NaN                   Cash   
37020            NaN          2           NaN           Installments   
13580            NaN  3  + Maid           NaN                   Cash   
17443            NaN         3            NaN  Cash or  Installments   
17275            NaN  4  + Maid           NaN           Installments   
1335     12 May 2024  4  + Maid           NaN                   Cash   
45620            NaN        3.0           NaN           Installments   
1711     11 May 2024         2            NaN           Installments   

                                                compound  city  \
49026  Village WestGiza, Sheikh Zayed City, Sheikh Za...   NaN   
41050  District 5Cairo, New Cairo City, The 5th Settl...   NaN   
51398  Swan Lake ResidenceCairo, New Cairo City, The ...   NaN   
37020  Palm Hills New CairoCairo, New Cairo City, The...   NaN   
13580  AllegriaGiza, Sheikh Zayed City, Sheikh Zayed ...   NaN   
17443              ShamasyNorth Coast, Sidi Abdel Rahman   NaN   
17275           MescaRed Sea, Hurghada, Safaga, Soma Bay   NaN   
1335   Badya Palm HillsGiza, 6 October City, 6 Octobe...   NaN   
45620  PX Palm HillsGiza, 6 October City, 6 October C...   NaN   
1711   Hyde ParkCairo, New Cairo City, The 5th Settle...   NaN   

                                                     dev  latitude  longitude  \
49026                      Cap Consulting(86 Properties)  31.02005   30.04809   
41050               Elshams Real Estate(1072 Properties)  31.42876   30.00865   
51398     Green Homes Real estate Agency(327 Properties)  31.46553   30.07392   
37020                   Blue Investments(514 Properties)  31.57952   30.01227   
13580                  Remax The Address(425 Properties)  30.95966   30.07129   
17443  سهم البورصة للاستثمار و التطوير العقاري(1640 P...  28.70343   31.00205   
17275       Egypt Best Properties West(10000 Properties)  33.96331   26.86433   
1335                  Circles investment(100 Properties)  30.67120   29.90930   
45620                      Vida Solution(920 Properties)  31.03969   29.99240   
1711        Egypt Best Properties West(10000 Properties)  31.55413   29.99592   

                                             description  \
49026  Apartment for sale in Village west compound Ar...   
41050  Apartment for Sale At District 5 – MarakezArea...   
51398  SWAN LAKE RESIDANCE SMALL TWINHOUSE FOR SALE B...   
37020  Unit details:HOT OPPORTUNITY in Palm Hills New...   
13580  Apartment for sale in Allegria ResidenceVery p...   
17443  Sidi Abdel Rahman, and thus Shamasy Village gi...   
17275  Developer : OlayanProject: Soma Bay (BLANCA)--...   
1335   Circles Real Estate Investment - Sheikh Zayed ...   
45620  Palm Hills developmentsP/X is located on the h...   
1711   For More Info : 01158239239Greens - Apartment ...   

                                                     url       price  size_m  \
49026  https://www.propertyfinder.eg/en/plp/buy/apart...  13000000.0   203.0   
41050  http



> **In this part, we ensure the accuracy of the regex data by validating the patterns meticulously. We experimented with various approaches to extract the complete word following the number, such as "month" or "year." However, due to the diversity in our patterns and descriptions, these methods presented numerous challenges and inconsistencies. To address this, we devised an alternative, more optimal solution. This approach efficiently handles the variations and ensures that the data extraction is reliable and accurate.**






In [73]:
# first here we try to get the word after our number to make sure its month or year and our patterns dont take wrong numbers
def handle_mistakes(disc,type_of_time):
  if type_of_time == "month":
    return re.split(r"[m]",disc,flags=re.IGNORECASE)

  elif type_of_time == "year" :
      return re.split(r"[y]",disc,flags=re.IGNORECASE)

def handle_number(row):
  return re.split(row["number"],row["description"],flags=re.IGNORECASE)[1][:5]



def handle_wrong_numbers(all_patterns,type_of_time):
  if type_of_time == "month":
    ins_al=all_patterns[all_patterns.notna()]

    correct_months=ins_al.apply(handle_mistakes,args=("month",))


    correct_months=correct_months.apply(lambda x:x[0] if len(x) == 2 else None).dropna()
    print("here we filtered our data with the values that have only m after its number")
    print(correct_months)
    print()
    correct_months_disc=combined_df.loc[correct_months.index,"description"]

    names=["description","number"]

    correct_months_handle=pd.concat([correct_months_disc,correct_months],names=names,axis=1) # we concatenate both of thim to use thim in our function to handle thim

    correct_months_handle.columns=names

    correct_months_handle["word"]=correct_months_handle.apply(handle_number,axis=1)
    print("here we get all the numbers with the word after it")
    print(correct_months_handle)

    print()
    print("the final result we get is dataframe that contain the number that suffix with month so now we make sure your data have high accuracy")
    print(correct_months_handle[correct_months_handle["word"].str.lower().str.lower().isin(["month","شهر","months"])])
    return correct_months_handle[correct_months_handle["word"].str.lower().str.lower().isin(["month","شهر","months"])]
  elif type_of_time == "year":
    ins_al=all_patterns[all_patterns.notna()]

    correct_years=ins_al.apply(handle_mistakes,args=("year",))


    correct_years=correct_years.apply(lambda x:x[0] if len(x) == 2 else None).dropna()
    print("here we filtered our data with the values that have only y after its number")
    print(correct_years)
    print()

    correct_years_disc=combined_df.loc[correct_years.index,"description"]

    names=["description","number"]

    correct_years_handle=pd.concat([correct_years_disc,correct_years],names=names,axis=1) # we concatenate both of thim to use thim in our function to handle thim

    correct_years_handle.columns=names

    correct_years_handle["word"]=correct_years_handle.apply(handle_number,axis=1)

    print("here we get all the numbers with the word after it")
    print(correct_years_handle)
    print()
    print("the final result we get is dataframe that contain the number that suffix with year so now we make sure your data have high accuracy")
    print(correct_years_handle[correct_years_handle["word"].str.lower().str.lower().isin(["year","سنة","years"])])

    return correct_years_handle[correct_years_handle["word"].str.lower().str.lower().isin(["year","سنة","years"])]









In [74]:
ok=handle_wrong_numbers(all_patterns,"year")

here we filtered our data with the values that have only y after its number
1         8 
5         6 
11       12 
12        8 
15        7 
        ... 
94216     7 
94320      8
96017     4 
96422     8 
96642     8 
Name: description, Length: 8185, dtype: object

here we get all the numbers with the word after it
                                             description number   word
1      MAVEN Development is launching at ras elhikma ...     8   years
5      For Sale in La Vista Ras El Hekma Sea View Cha...     6   years
11     Chalet for sale with installments in Crystals ...    12   Years
12     Marseilia Beach 5 Location : km210 - Ras El-He...     8   years
15     Apartment 107 sqm, two roomsView on the landsc...     7   sqm, 
...                                                  ...    ...    ...
94216  158 sqm apartment for sale in West 6th of Octo...     7   years
94320  Apartments for sale10%Down Payment Over 8Years...      8  Years
96017  Townhouse resale, Ready to move in T

In [75]:
# now its time to concat thim in our column
inst_in_m=handle_wrong_numbers(all_patterns,"month")
inst_in_m=inst_in_m["number"].astype(int)/12

inst_in_y=handle_wrong_numbers(all_patterns,"year")
inst_in_y=inst_in_y["number"].astype(int)

here we filtered our data with the values that have only m after its number
136       30 
182       18 
433      000 
713       18 
867       60 
         ... 
88536     90 
89325      3 
92525     18 
93989    600 
93994      6 
Name: description, Length: 476, dtype: object

here we get all the numbers with the word after it
                                             description number   word
136    Apartment 198 square metersA mini compound in ...    30   month
182    Balkan Beach Resort is a contemporary haven in...    18   month
433    RESALE AT belle vie Emaar , 2 bedrooms apartme...   000   milli
713    --- Inter Breeze Complex.Location: - -\tInterC...    18   month
867    Apartment For sale In Beit Watan First Distric...    60   month
...                                                  ...    ...    ...
88536  Apartment for sale in Lugar Compound by Gates ...    90   month
89325  Town house for sale 10% DP |Hacienda Heneish |...     3   bedro
92525  Very special sandy private

In [76]:
print("the months converted to year to ensure consistency")
print(inst_in_m)
print("the years of installments")
inst_in_y = pd.concat([inst_in_y, inst_in_m])
print(inst_in_y) # now here we have all installments we extract from here

the months converted to year to ensure consistency
136      2.500000
182      1.500000
713      1.500000
867      5.000000
899      5.833333
           ...   
83013    1.666667
83284    3.000000
83344    3.333333
88536    7.500000
92525    1.500000
Name: number, Length: 302, dtype: float64
the years of installments
1         8.000000
5         6.000000
11       12.000000
12        8.000000
18        7.000000
           ...    
83013     1.666667
83284     3.000000
83344     3.333333
88536     7.500000
92525     1.500000
Name: number, Length: 7334, dtype: float64


In [77]:
inst_in_y

1         8.000000
5         6.000000
11       12.000000
12        8.000000
18        7.000000
           ...    
83013     1.666667
83284     3.000000
83344     3.333333
88536     7.500000
92525     1.500000
Name: number, Length: 7334, dtype: float64

In [78]:
combined_df["installment_years"] = inst_in_y

In [79]:
inst_in_y.value_counts()

number
8.000000        3090
7.000000        1338
6.000000         813
10.000000        594
5.000000         552
9.000000         276
4.000000         271
3.000000         114
2.000000          51
1.500000          51
3.333333          34
0.250000          25
30.000000         20
0.500000          15
12.000000         14
2.500000          10
4.166667           7
4.500000           6
1.000000           6
11.000000          5
70.000000          5
35.000000          4
20.000000          3
1508.000000        2
50.000000          2
5508.000000        2
1.666667           2
3.500000           2
16.000000          1
508.000000         1
4008.000000        1
7008.000000        1
5.833333           1
1008.000000        1
2032.000000        1
7508.000000        1
1007.000000        1
135.000000         1
17.000000          1
9008.000000        1
7504.000000        1
8.333333           1
1.750000           1
7.916667           1
8.500000           1
4.583333           1
23583.333333       1
7.5000

In [80]:
combined_df['installment_years']=combined_df[combined_df['installment_years'] <= 10]['installment_years']

>**here we did that to avoid getting the wrong numbers from regex**

### payment method

In [81]:
combined_df["Payment method"].value_counts()

Payment method
Cash                     17478
Installments             12935
Cash or  Installments     9432
Name: count, dtype: int64

In [82]:
combined_df[(combined_df["Payment method"] == "Cash") & (combined_df["Down payment"] != -1)] # now for consisity this all should be converted to cash or installment

Property Size  Down payment Bathrooms Property Type  \
2       1,862 sqft / 173 sqm     7000000.0         3     Apartment   
8       3,305 sqft / 307 sqm     4000000.0         4         Villa   
23      1,938 sqft / 180 sqm     3712500.0         2     Apartment   
98      1,507 sqft / 140 sqm     2100000.0         2     Apartment   
99      1,776 sqft / 165 sqm     3954784.0         3     Apartment   
...                      ...           ...       ...           ...   
94252   5,382 sqft / 500 sqm     8370000.0         3         Villa   
94428   5,382 sqft / 500 sqm     8370000.0         3         Villa   
95739   5,382 sqft / 500 sqm     8370000.0       3.0         Villa   
95765   3,714 sqft / 345 sqm     5070000.0       2.0         Villa   
96677   2,422 sqft / 225 sqm     3821000.0         2         Villa   

      Available from   Bedrooms  Property age Payment method  \
2                NaN  3  + Maid           NaN           Cash   
8                NaN  4  + Maid           NaN           Cash   
23               NaN  3  + Maid           NaN           Cash   
98               NaN         2            NaN           Cash   
99               NaN         3            NaN           Cash   
...              ...        ...           ...            ...   
94252            NaN          5           NaN           Cash   
94428            NaN         5            NaN           Cash   
95739            NaN          5           NaN           Cash   
95765            NaN          4           NaN           Cash   
96677            NaN         3            NaN           Cash   

                                                compound  city  ...  latitude  \
2      Palm Hills New CairoCairo, New Cairo City, The...   NaN  ...  31.57952   
8            Silver SandsNorth Coast, Qesm Marsa Matrouh   NaN  ...  27.37944   
23     The Address EastCairo, New Cairo City, The 5th...   NaN  ...  31.57726   
98     Mountain View Hyde ParkCairo, New Cairo City, ...   NaN  ...  31.55557   
99     Mountain View iCityCairo, New Cairo City, The ...   NaN  ...  31.59974   
...                                                  ...   ...  ...       ...   
94252  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   
94428  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   
95739  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   
95765  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   
96677  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   

       longitude                                        description  \
2       30.01227  Project Name: Palm Hills New Cairo Developer N...   
8       31.26528  Silver Sands - North CoastFor More Details Con...   
23      30.07132  Apartment for sale in The Address East Compoun...   
98      29.98756  Area: 140 mRooms:2Bathrooms:2Down payment: 2,1...   
99      30.06942  Property Details:Very Prime Location Apartment...   
...          ...                                                ...   
94252   30.04858  The Wondermark Compound - Future Cityـــــــــ...   
94428   30.04858  The Wondermark Compound - Future Cityـــــــــ...   
95739   30.04858  The Wondermark Compound - Future Cityـــــــــ...   
95765   30.04858  The Wondermark Compound - Future Cityـــــــــ...   
96677   30.04858  The Wondermark Compound - Future Cityـــــــــ...   

                                                     url       price  size_m  \
2      https://www.propertyfinder.eg/en/plp/buy/apart...  10300000.0   173.0   
8      https://www.propertyfinder.eg/en/plp/buy/villa...  40000000.0   307.0   
23     https://www.propertyfinder.eg/en/plp/buy/apart...   4050000.0   180.0   
98     https://www.propertyfinder.eg/en/plp/buy/apart...   2100000.0   140.0   
99     https://www.propertyfinder.eg/en/plp/buy/apart...   3954784.0   165.0   
...                                                  ...         ...     ...   
94252  https://www.

#### modify the rows we found that its down payment into cash or installment instead of only cash

In [83]:
combined_df.loc[(combined_df["Payment method"] == "Cash") & (combined_df["Down payment"] != -1),"Payment method"]= "Cash\xa0or \xa0Installments"
# Correcting data extracted from web scraping: update payment methods where necessary

In [84]:
combined_df["Payment method"].value_counts()

Payment method
Cash or  Installments    13778
Cash                     13132
Installments             12935
Name: count, dtype: int64

In [85]:
combined_df.columns

Index(['Property Size', 'Down payment', 'Bathrooms', 'Property Type',
       'Available from', 'Bedrooms', 'Property age', 'Payment method',
       'compound', 'city', 'dev', 'latitude', 'longitude', 'description',
       'url', 'price', 'size_m', 'price/met', 'spec_comp', 'Region',
       'installment_years'],
      dtype='object')

### add furnished and finished column



> **I found that  the propety finder dont get the information in a right way so i prefer i get it from the descreption of our data**



In [86]:
def extract_finished(description):
    patterns = [
        r"(fully|semi|un|Super Luxe?)\s*finishing",
        r"(fully|semi|un|Super Luxe?)\s*finished",
        r"التشطيب\s*:\s*(\w*)",
        r"التشطيب\s*:\s*(كامل|جزئي|بدون)",
        r"(decorated|undecorated)",
        r"(turnkey|move-in\s*ready|ready\s*to\s*move\s*in)"
    ]
    for pattern in patterns:
        match = re.search(pattern, description, flags=re.IGNORECASE)
        if match:
            return match.group(1).strip()
    return None
all_pat_fin=combined_df["description"].apply(extract_finished)
all_pat_fin[all_pat_fin.notnull()]

1                   FULLY
4                   Fully
7                   Fully
11                  Fully
12                  fully
               ...       
95270               Fully
96017    Ready to move in
96718               Fully
96727               Fully
96735               fully
Name: description, Length: 17531, dtype: object

In [87]:
category_mapping = {
    # Fully finished
    "Fully": "fully",
    "fully": "fully",
    "FULLY": "fully",
    "Ready to move in": "fully",
    "Ready To Move  in": "fully",
    "Ready To Move in": "fully",
    "Ready to move  in": "fully",
    "ready to moveIn": "fully",
    "Ready to moveIn": "fully",
    "Ready To moveIn": "fully",
    "READY TO MOVE IN": "fully",
    "Ready to Move in": "fully",
    "Ready To Move In": "fully",
    "ready to move  in": "fully",
    "Ready to MoveIn": "fully",
    "move-in ready": "fully",
    "Move-in ready": "fully",
    "Turnkey": "fully",
    "decorated": "fully",
    "تشطيب": "fully",
    "متشطبه": "fully",
    "متشطب": "fully",
    "كامل": "fully",
    "FUlly": "fully",
    "ready to move  In": "fully",
    "ready to move in" :"fully",
    "Ready to Move In" :"fully",

    # Semi finished
    "Semi": "semi",
    "semi": "semi",
    "نصف": "semi",
    "SEMI": "semi",
    "نص": "semi",
    "SemI": "semi",

    # Super Luxe finished
    "Super Luxe": "super lux",
    "Super Lux": "super lux",
    "super lux": "super lux",
    "Super lux": "super lux",
    "Super luxe": "super lux",
    "super luxe": "super lux",
    "Super LUX": "super lux",
    "super LUX": "super lux",
    "SUPER LUX": "super lux",
    "سوبر": "super lux",
    "فاخر": "super lux",
    "ألترا": "super lux",
    "كاملة": "super lux",
    "super Lux": "super lux",

    # Unfinished
    "Un": "unfinished",
    "un": "unfinished",
    "core": "unfinished",
    "محارهالتسليم": "unfinished",
    "طوب": "unfinished",
    "3": "unfinished",
}

# Apply the mapping to the series
all_pat_fin=all_pat_fin[~(all_pat_fin=='')]
all_pat_fin = all_pat_fin.replace(category_mapping)

# Verify the changes
print(all_pat_fin.value_counts())

description
fully         14388
semi           2490
super lux       594
unfinished       50
Name: count, dtype: int64


In [88]:

def extract_furnished(description):
    patterns = [
        r"(fully|semi|un|Super Luxe?)\s*furnished",               # fully, semi, unfurnished
        r"(furnished|partially furnished|unfurnished|Super Luxe?)", # furnishing status
        r"(مفروشة\s*تماماً|مفروشة\s*جزئياً|غير\s*مفروشة)" , # Arabic equivalents
        r"(includes\s*furniture|with\s*furniture|without\s*furniture)", # mentions of furniture
        r"(completely|partly|not)\s*furnished"       # alternate terms for fully and semi
    ]
    for pattern in patterns:
        match = re.search(pattern, description, flags=re.IGNORECASE)
        if match:
            return match.group(1).strip()
    return None

all_pat_furnish=combined_df["description"].apply(extract_furnished)
all_pat_furnish[all_pat_furnish.notnull()]

7        super luxe
9             fully
18            fully
25        Super Lux
112           Fully
            ...    
93820     Super Lux
93833     super lux
94068         Fully
94307     furnished
96465     super lux
Name: description, Length: 3341, dtype: object

In [89]:
category_mapping = {
    # Fully furnished
    "Fully": "fully furnished",
    "fully": "fully furnished",
    "Furnished": "fully furnished",
    "furnished": "fully furnished",
    "with furniture": "fully furnished",
    "With furniture": "fully furnished",
    "with Furniture": "fully furnished",
    "With Furniture": "fully furnished",
    "includes furniture": "fully furnished",
    "includes Furniture": "fully furnished",
    "FURNISHED": "fully furnished",
    "WITH FURNITURE": "fully furnished",
    "FULLY": "fully furnished",

    # Semi-furnished
    "Semi": "semi-furnished",
    "semi": "semi-furnished",
    "partially furnished": "semi-furnished",

    # Super lux
    "Super Lux": "super lux",
    "super lux": "super lux",
    "Super Luxe": "super lux",
    "Super lux": "super lux",
    "Super LUX": "super lux",
    "super Luxe": "super lux",
    "super LUX": "super lux",
    "SUPER LUX": "super lux",
    "Super LuxE": "super lux",
    "super luxe": "super lux",
    "Super luxe": "super lux",
    "super Lux": "super lux",

    # Unfurnished
    "Un": "unfurnished",
    "un": "unfurnished",
    "without furniture": "unfurnished",
    "Without furniture": "unfurnished",
    "without Furniture": "unfurnished",
    "Without Furniture": "unfurnished",
    "غير مفروشة": "unfurnished",
    "UN": "unfurnished"
}
# Apply the mapping to the series
all_pat_furnish=all_pat_furnish[~(all_pat_furnish=='')]
all_pat_furnish = all_pat_furnish.replace(category_mapping)

# Verify the changes
print(all_pat_furnish.value_counts())

description
super lux          1805
fully furnished    1382
unfurnished          89
semi-furnished       65
Name: count, dtype: int64




### handle the bedroom and bathrooms columns



In [90]:
copy2_df=combined_df.copy()
copy2_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 40159 entries, 0 to 96749
Data columns (total 21 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Property Size      40159 non-null  object 
 1   Down payment       40159 non-null  float64
 2   Bathrooms          40150 non-null  object 
 3   Property Type      40159 non-null  object 
 4   Available from     3862 non-null   object 
 5   Bedrooms           40131 non-null  object 
 6   Property age       154 non-null    float64
 7   Payment method     39845 non-null  object 
 8   compound           40159 non-null  object 
 9   city               0 non-null      float64
 10  dev                40159 non-null  object 
 11  latitude           40156 non-null  float64
 12  longitude          40156 non-null  float64
 13  description        40159 non-null  object 
 14  url                40159 non-null  object 
 15  price              40159 non-null  float64
 16  size_m             40159 no

In [91]:
copy2_df["Bedrooms"]=copy2_df["Bedrooms"].astype(str).str.strip() # ok its more effeceint way to do this
copy2_df["Bedrooms"]

0                3
1        2  + Maid
2        3  + Maid
3                3
4        3  + Maid
           ...    
96700            3
96718            3
96727    4  + Maid
96735    2  + Maid
96749            4
Name: Bedrooms, Length: 40159, dtype: object

In [92]:
try_this=copy2_df[copy2_df["Bedrooms"].str.contains("Maid")]["Bedrooms"].str.replace('  + Maid','').str.replace('+','')
try_this=try_this[try_this!='studio']
try_this=try_this.astype(float) + 1
copy2_df.loc[try_this.index,"Bedrooms"]=try_this

In [93]:
copy2_df["Bedrooms"].value_counts()

Bedrooms
3                 10961
2                  6206
4                  4674
3.0                2763
4.0                2700
5                  1935
4.0                1871
5.0                1600
1                  1519
2.0                1380
3.0                1060
5.0                 836
6                   554
6.0                 508
1.0                 330
studio              224
6.0                 221
2.0                 208
7                   164
7.0                 142
8.0                 109
7.0                  71
8                    33
nan                  28
studio  + Maid       26
8.0                  24
7+                   12
Name: count, dtype: int64

In [94]:
copy2_df['Bedrooms']=copy2_df['Bedrooms'].astype(str).str.replace('studio  + Maid','').str.replace('studio','').str.replace('7+','7')
copy2_df['Bedrooms']=copy2_df[copy2_df['Bedrooms'] != '']["Bedrooms"].astype(float)
copy2_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 40159 entries, 0 to 96749
Data columns (total 21 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Property Size      40159 non-null  object 
 1   Down payment       40159 non-null  float64
 2   Bathrooms          40150 non-null  object 
 3   Property Type      40159 non-null  object 
 4   Available from     3862 non-null   object 
 5   Bedrooms           39881 non-null  float64
 6   Property age       154 non-null    float64
 7   Payment method     39845 non-null  object 
 8   compound           40159 non-null  object 
 9   city               0 non-null      float64
 10  dev                40159 non-null  object 
 11  latitude           40156 non-null  float64
 12  longitude          40156 non-null  float64
 13  description        40159 non-null  object 
 14  url                40159 non-null  object 
 15  price              40159 non-null  float64
 16  size_m             40159 no

In [95]:
copy2_df["Bedrooms"].unique()

array([ 3.,  4.,  5.,  2.,  6.,  1.,  7.,  8., nan])

now we are sure that we are convert the bedroom to float and get its values also we add the maid as its normal bedroom

In [96]:
copy2_df["Bathrooms"]=copy2_df["Bathrooms"].astype(str).str.strip()
copy2_df["Bathrooms"].unique()

array(['2', '3', '4', '1', '6', '7+', '5', '7', 'none', 'nan', '3.0',
       '2.0', '5.0', '4.0', '1.0', '6.0', '7.0'], dtype=object)

In [97]:
copy2_df["Bathrooms"]=copy2_df["Bathrooms"].astype(str).str.replace('7+','7')
copy2_df["Bathrooms"]=copy2_df[(copy2_df["Bathrooms"] != 'nan') & (copy2_df["Bathrooms"] != 'none')]["Bathrooms"].astype(float)
copy2_df["Bathrooms"].unique()


array([ 2.,  3.,  4.,  1.,  6.,  7.,  5., nan])

In [98]:
pd.pivot_table(copy2_df, values='price', index=['Bedrooms','Bathrooms'], aggfunc='median')

price
Bedrooms Bathrooms            
1.0      1.0         5600000.0
         2.0         6850000.0
         3.0         6000000.0
2.0      1.0         5710000.0
         2.0         8050000.0
         3.0         8269706.0
         4.0        12000000.0
3.0      1.0         5600000.0
         2.0         8200000.0
         3.0         9500300.0
         4.0        13940000.0
         5.0        20000000.0
         6.0        17606970.0
         7.0        20540000.0
4.0      1.0         8000000.0
         2.0         9594000.0
         3.0        12283192.0
         4.0        17000000.0
         5.0        20000000.0
         6.0        20000000.0
         7.0        46916085.0
5.0      1.0         8642000.0
         2.0        15000000.0
         3.0        14000000.0
         4.0        18500000.0
         5.0        24100000.0
         6.0        27000000.0
         7.0        31508004.0
6.0      1.0        23000000.0
         2.0        28000000.0
         3.0        18000000.0
         4.0        20600000.0
         5.0        26000000.0
         6.0        36057150.0
         7.0        46625000.0
7.0      2.0         6400000.0
         3.0        25799000.0
         4.0        30000000.0
         5.0        28000000.0
         6.0        38075000.0
         7.0        56750000.0
8.0      4.0        26000000.0
         5.0        28000000.0
         6.0        46800000.0
         7.0        55000000.0

### try to analyse the down payment column

In [99]:
down_pay_df=combined_df[combined_df["Down payment"] != -1]
down_pay_df

Property Size  Down payment Bathrooms Property Type  \
0       1,593 sqft / 148 sqm      865000.0         2     Apartment   
1        1,023 sqft / 95 sqm           0.0         2        Chalet   
2       1,862 sqft / 173 sqm     7000000.0         3     Apartment   
5       1,615 sqft / 150 sqm     2400000.0         2        Chalet   
8       3,305 sqft / 307 sqm     4000000.0         4         Villa   
...                      ...           ...       ...           ...   
96642   1,927 sqft / 179 sqm     3000000.0         3     Apartment   
96677   2,422 sqft / 225 sqm     3821000.0         2         Villa   
96700   1,722 sqft / 160 sqm     1005000.0         3     Apartment   
96718   2,024 sqft / 188 sqm     2300000.0         2        Chalet   
96749   2,314 sqft / 215 sqm      944500.0         4     Townhouse   

      Available from   Bedrooms  Property age         Payment method  \
0                NaN         3            NaN  Cash or  Installments   
1        15 May 2024  2  + Maid           NaN  Cash or  Installments   
2                NaN  3  + Maid           NaN  Cash or  Installments   
5        14 May 2024  3  + Maid           NaN           Installments   
8                NaN  4  + Maid           NaN  Cash or  Installments   
...              ...        ...           ...                    ...   
96642            NaN          5           NaN           Installments   
96677            NaN         3            NaN  Cash or  Installments   
96700            NaN          3           NaN  Cash or  Installments   
96718            NaN          3           NaN           Installments   
96749            NaN         4            NaN           Installments   

                                                compound  city  ...  latitude  \
0      Verona CompoundCairo, Mokattam, Al Hadaba Al W...   NaN  ...  31.32294   
1                    Cali CoastNorth Coast, Ras Al Hekma   NaN  ...  28.10030   
2      Palm Hills New CairoCairo, New Cairo City, The...   NaN  ...  31.57952   
5         La vista Ras El HikmaNorth Coast, Ras Al Hekma   NaN  ...  27.99701   
8            Silver SandsNorth Coast, Qesm Marsa Matrouh   NaN  ...  27.37944   
...                                                  ...   ...  ...       ...   
96642  Hyde ParkCairo, New Cairo City, The 5th Settle...   NaN  ...  31.55413   
96677  The Wonder MarqCairo, Mostakbal City - Future ...   NaN  ...  31.64085   
96700  MonarkCairo, Mostakbal City - Future City, Mos...   NaN  ...  31.63880   
96718        Silver SandsNorth Coast, Qesm Marsa Matrouh   NaN  ...  27.37944   
96749  Garden LakesGiza, 6 October City, 6 October Co...   NaN  ...  31.03008   

       longitude                                        description  \
0       29.99035  Apartment for sale in the AL HADABA AL WOSTA:3...   
1       31.08714  MAVEN Development is launching at ras elhikma ...   
2       30.01227  Project Name: Palm Hills New Cairo Developer N...   
5       31.09140  For Sale in La Vista Ras El Hekma Sea View Cha...   
8       31.26528  Silver Sands - North CoastFor More Details Con...   
...          ...                                                ...   
96642   29.99592  for sale in Hyde park new Cairo Apartment spac...   
96677   30.04858  The Wondermark Compound - Future Cityـــــــــ...   
96700   30.06985  -Apartment in MONARK Compound in Mostakbal Cit...   
96718   31.26528  Project Name: Silver SandsDeveloper: Ora* Chal...   
96749   29.98799  Area : 6th of October CityProject : Garden lak...   

                                                     url       price  size_m  \
0      https://www.propertyfinder.eg/en/plp/buy/apart...   2486400.0   148.0   
1      https://www.propertyfinder.eg/en/plp/buy/chale...   8200000.0    95.0   
2      https://www.propertyfinder.eg/en/plp/buy/apart...  10300000.0   173.0   
5      https://www.propertyfinder.eg/en/plp/buy/chale...  16000000.0   150.0   
8      https://www.propertyfinder.eg/en/plp/buy/villa...  40000000.0   307.0   
...

In [100]:
max_value = 7000000
bin_edges = range(0, max_value, 500000)

down_pay_df["Down payment"]=down_pay_df["Down payment"].sort_values()

down_pay_df["Down payment_f"]=pd.cut(down_pay_df["Down payment"], bins=bin_edges)

max_value_year = 12
bin_edges = range(0, max_value_year)

down_pay_df["installment_years"]=down_pay_df["installment_years"].sort_values()

down_pay_df["installment_years_f"]=pd.cut(down_pay_df["installment_years"], bins=bin_edges)

years_mapping = {
        "(0, 1]": "1 year",
        "(1, 2]": "2 years",
        "(2, 3]": "3 years",
        "(3, 4]": "4 years",
        "(4, 5]": "5 years",
        "(5, 6]": "6 years",
        "(6, 7]": "7 years",
        "(7, 8]": "8 years",
        "(8, 9]": "9 years",
        "(9, 10]": "10 years",
        "(10, 11]": "11 years"
    }

down_pay_df["installment_years_f"] = down_pay_df["installment_years_f"].astype(str)
down_pay_df["installment_years_f"] = down_pay_df["installment_years_f"].replace(years_mapping)
down_pay_df["installment_years_f"] = down_pay_df[down_pay_df["installment_years_f"] != 'nan']["installment_years_f"]




In [101]:
pivot = pd.pivot_table(down_pay_df, index=['Down payment_f', 'installment_years_f'], aggfunc='size')
pivot = pivot.rename("count").reset_index()
category_mapping = {
        "(0, 500000]": "0-0.5M",
        "(500000, 1000000]": "0.5-1M",
        "(1000000, 1500000]": "1-1.5M",
        "(1500000, 2000000]": "1.5-2M",
        "(2000000, 2500000]": "2-2.5M",
        "(2500000, 3000000]": "2.5-3M",
        "(3000000, 3500000]": "3-3.5M",
        "(3500000, 4000000]": "3.5-4M",
        "(4000000, 4500000]": "4-4.5M",
        "(4500000, 5000000]": "4.5-5M",
        "(5000000, 5500000]": "5-5.5M",
        "(5500000, 6000000]": "5.5-6M",
        "(6000000, 6500000]": "6-6.5M",
}

pivot['Down payment_f'] = pivot['Down payment_f'].astype(str)
pivot['Down payment_f'] = pivot['Down payment_f'].replace(category_mapping)

fig = px.bar(pivot, x="Down payment_f", y="count", color="installment_years_f", barmode='group')

fig

## create some data frames for specific plots

In [147]:
map_df = combined_df[(combined_df["latitude"] != 5) & 
                     (combined_df["longitude"] != 6) & 
                     (combined_df["price"].notnull())]

In [145]:
size_df=combined_df[combined_df["size_m"] <= 500]

In [146]:

max_value = int(size_df["size_m"].max())
bin_edges = range(0, max_value + 50, 50)


size_df = size_df.sort_values(by='size_m')


size_df["size_m_f"] = pd.cut(size_df["size_m"], bins=bin_edges)

bins = ['(0, 50]', '(50, 100]', '(100, 150]', '(150, 200]', '(200, 250]', '(250, 300]', '(300, 350]', '(350, 400]', '(400, 450]', '(450, 500]']
names = ['0-50', '51-100', '101-150', '151-200', '201-250', '251-300', '301-350', '351-400', '401-450', '451-500']

dic=dict(zip(bins,names))

size_df["size_m_f"]=size_df["size_m_f"].astype(str)
size_df["size_m_f"]=size_df["size_m_f"].replace(dic)

In [105]:
size_df["size_m_f"].unique()

array(['0-50', '51-100', '101-150', '151-200', '201-250', '251-300',
       '301-350', '351-400', '401-450', '451-500'], dtype=object)

# work in rent data

In [107]:
path="E:\Egyption houses rent" # the path of the file

dataframes=[] # our list which i will use to save all the dataframes

for file_name in os.listdir(path): # get all the file names
  real_path=os.path.join(path,file_name) # get the real path we will use to fitch the csv
  df=pd.read_csv(real_path) # read it
  dataframes.append(df) # add it to the list

combined_df_r = pd.concat(dataframes, ignore_index=True)  # use concat to combine thin in index axis and ignore the index


In [108]:
combined_df_r.drop_duplicates(subset=['url'],inplace=True)
combined_df_r.info()  # wow now we have 7886

<class 'pandas.core.frame.DataFrame'>
Index: 28271 entries, 0 to 31456
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    363 non-null    float64
 1   Bathrooms       26879 non-null  object 
 2   Bedrooms        26878 non-null  object 
 3   Property Type   28271 non-null  object 
 4   Available from  396 non-null    object 
 5   Property Size   26879 non-null  object 
 6   compound        28271 non-null  object 
 7   dev             28271 non-null  object 
 8   latitude        28271 non-null  int64  
 9   longitude       28271 non-null  int64  
 10  description     28271 non-null  object 
 11  url             28271 non-null  object 
 12  price           28271 non-null  object 
dtypes: float64(1), int64(2), object(10)
memory usage: 3.0+ MB


## handle the price column in rent data 

In [109]:
combined_df_r=combined_df_r[combined_df_r['price'] != 'unknown']

In [110]:

combined_df_r['price']=combined_df_r['price'].str.replace(',','').str.replace('EGP/month','').str.strip().astype(float)
combined_df_r.info()

<class 'pandas.core.frame.DataFrame'>
Index: 28270 entries, 0 to 31456
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    363 non-null    float64
 1   Bathrooms       26879 non-null  object 
 2   Bedrooms        26878 non-null  object 
 3   Property Type   28270 non-null  object 
 4   Available from  396 non-null    object 
 5   Property Size   26879 non-null  object 
 6   compound        28270 non-null  object 
 7   dev             28270 non-null  object 
 8   latitude        28270 non-null  int64  
 9   longitude       28270 non-null  int64  
 10  description     28270 non-null  object 
 11  url             28270 non-null  object 
 12  price           28270 non-null  float64
dtypes: float64(2), int64(2), object(9)
memory usage: 3.0+ MB


In [112]:
combined_df_r= combined_df_r[ (combined_df_r['price'] < 1000000) & (combined_df_r['price'] >= 3000)]
combined_df_r.info()

<class 'pandas.core.frame.DataFrame'>
Index: 28020 entries, 0 to 31456
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    362 non-null    float64
 1   Bathrooms       26654 non-null  object 
 2   Bedrooms        26654 non-null  object 
 3   Property Type   28020 non-null  object 
 4   Available from  394 non-null    object 
 5   Property Size   26654 non-null  object 
 6   compound        28020 non-null  object 
 7   dev             28020 non-null  object 
 8   latitude        28020 non-null  int64  
 9   longitude       28020 non-null  int64  
 10  description     28020 non-null  object 
 11  url             28020 non-null  object 
 12  price           28020 non-null  float64
dtypes: float64(2), int64(2), object(9)
memory usage: 3.0+ MB


In [113]:
combined_df_r.info()

<class 'pandas.core.frame.DataFrame'>
Index: 28020 entries, 0 to 31456
Data columns (total 13 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    362 non-null    float64
 1   Bathrooms       26654 non-null  object 
 2   Bedrooms        26654 non-null  object 
 3   Property Type   28020 non-null  object 
 4   Available from  394 non-null    object 
 5   Property Size   26654 non-null  object 
 6   compound        28020 non-null  object 
 7   dev             28020 non-null  object 
 8   latitude        28020 non-null  int64  
 9   longitude       28020 non-null  int64  
 10  description     28020 non-null  object 
 11  url             28020 non-null  object 
 12  price           28020 non-null  float64
dtypes: float64(2), int64(2), object(9)
memory usage: 3.0+ MB


## handle compound column in rent data

In [114]:
# to explore the data in our data we will do that
split_compound_r=combined_df_r["compound"].str.split(',',expand=True)
split_compound_r = split_compound_r.fillna('Not mentioned')
px.treemap(split_compound_r,path=[0,1,2,3])

In [115]:
split_compound_r.loc[split_compound_r[split_compound_r[1] == "Not mentioned"][0].str.split("Cairo|North Coast|Giza|Alexandria|Qalyubia",expand=True)[0].index,1]=split_compound_r[split_compound_r[1] == "Not mentioned"][0].str.split("Cairo|North Coast|Giza|Alexandria|Qalyubia",expand=True)[0]
split_compound_r[1]=split_compound_r[1].str.strip()
split_compound_r[1].replace({'New':"New Cairo City"},inplace=True)


In [116]:
split_compound_r[1].value_counts()

1
New Cairo City       12095
Sheikh Zayed City     2961
6 October City        2540
Hay El Maadi          1825
Madinaty              1678
                     ...  
Bab Al Molouk St.        1
Hay Gharb                1
Sidi Heneish             1
Hay Shobra               1
El Esmailiya City        1
Name: count, Length: 83, dtype: int64

In [117]:
com_comp = split_compound_r[1][split_compound_r[1].isin(split_compound[1])]
print(com_comp.unique())

['6 October City' 'Madinaty' 'Sheikh Zayed City' 'Hadayek El Ahram'
 'Nasr City' 'Hay Sharq' 'Heliopolis - Masr El Gedida' 'New Cairo City'
 'Dokki' 'Hay El Maadi' 'Al Agouza' 'Hay El Manial' 'Obour City'
 'El Nozha' 'Hay El Haram' 'Sidi Abdel Rahman' 'Shorouk City'
 'Mohandessin' 'Hay Wasat' 'Al Alamein' 'Zamalek' 'Ganoub El Giza'
 'Hay Torah' 'Qesm Marsa Matrouh' 'Hay Awal El Montazah' 'New Heliopolis'
 'Mokattam' 'Al Mansoura' 'Ras Al Hekma' 'New Capital City'
 'Hay Than El Montazah' 'Hurghada' 'Garden City'
 'Cairo - Ismailia Desert Road' 'Mostakbal City - Future City'
 'Hay Al Amereyah' 'Alexandria Compounds' 'Hay Boulaq El-Dakrour'
 'Qesm Ad Dabaah' 'Ring Road' 'Cairo Alexandria Desert Road'
 'Al Ain Al Sokhna' 'Fuka' 'El Khalifa' 'Sharm El Sheikh'
 'Qesm Borg El Arab' 'Borg El Arab City' 'HurghadaRed Sea' ''
 'Porto SaidPort Saeed' 'North Coast Resorts' 'Hacienda' 'Badr City'
 'Hay El Zaytoun' 'Dar El Salam' 'Coronado' 'Hay Masr El Kadima'
 'Markaz Al Hamam' 'New Alamein City' '

In [118]:
combined_df_r['Region'] = split_compound_r[1]
combined_df_r['spec_Compound'] = split_compound_r[0]

In [119]:
combined_df_r['Region'].replace('','North Coast',inplace=True)

In [120]:
pivot_comp=pd.pivot_table(combined_df_r, values='price', index=['Region'], aggfunc='median')

pivot_comp['house_count']=combined_df_r.groupby(['Region']).size()


filtered_pivot_comp = pivot_comp[pivot_comp['house_count'] >= 10]

largest_regions = filtered_pivot_comp.nlargest(10, columns='price').sort_values(by='price', ascending=True)
smallest_regions = filtered_pivot_comp.nsmallest(10, columns='price')

  # Create subplots
fig = make_subplots(rows=2,vertical_spacing=0.5, cols=1, subplot_titles=("Top 10 Regions by Price", "Bottom 10 Regions by Price"))

  # Plot largest regions
fig.add_trace(
      go.Scatter(x=largest_regions.index, y=largest_regions['price'], mode='markers+lines', name='Largest Regions'),
      row=1, col=1
)

  # Plot smallest regions
fig.add_trace(
      go.Scatter(x=smallest_regions.index, y=smallest_regions['price'], mode='markers+lines', name='Smallest Regions'),
      row=2, col=1
)

  # Update layout
fig.update_layout(
      title_text="Region Price Analysis",
      height=500,
      width=1300
)

fig.update_xaxes(row=1, col=1)
fig.update_yaxes(title_text="rent", row=1, col=1)

fig.update_xaxes(title_text="Region", row=2, col=1)
fig.update_yaxes(title_text="rent", row=2, col=1)

## handle the size column

In [121]:
combined_df_r['size_m']=combined_df_r['Property Size'].str.split().str[3].str.replace(',', '').str.strip() 
combined_df_r['size_m']=combined_df_r['size_m'].astype(float)
combined_df_r['size_m']

0        196.0
1        140.0
2          NaN
3        130.0
4        550.0
         ...  
31452    120.0
31453    118.0
31454    192.0
31455    155.0
31456     74.0
Name: size_m, Length: 28020, dtype: float64

In [122]:
combined_df_r=combined_df_r[~(combined_df_r['size_m'] > 2000) & ~(combined_df_r['size_m'] <=22 )]

>**after manuel exploration we found that the sizes that bigger than 1500 is exist but it refer to the land area more than the building area**

In [123]:
px.scatter(combined_df_r,x='size_m',y='price')

In [124]:
combined_df_r.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27946 entries, 0 to 31456
Data columns (total 16 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    362 non-null    float64
 1   Bathrooms       26580 non-null  object 
 2   Bedrooms        26580 non-null  object 
 3   Property Type   27946 non-null  object 
 4   Available from  394 non-null    object 
 5   Property Size   26580 non-null  object 
 6   compound        27946 non-null  object 
 7   dev             27946 non-null  object 
 8   latitude        27946 non-null  int64  
 9   longitude       27946 non-null  int64  
 10  description     27946 non-null  object 
 11  url             27946 non-null  object 
 12  price           27946 non-null  float64
 13  Region          27946 non-null  object 
 14  spec_Compound   27946 non-null  object 
 15  size_m          26580 non-null  float64
dtypes: float64(3), int64(2), object(11)
memory usage: 3.6+ MB


In [125]:

max_value = int(combined_df_r["size_m"].max())
bin_edges = range(0, max_value + 200,200)


combined_df_r = combined_df_r.sort_values(by='size_m')


combined_df_r["size_m_f"] = pd.cut(combined_df_r["size_m"], bins=bin_edges)
combined_df_r["size_m_f"]=combined_df_r["size_m_f"].astype(str)

In [126]:
bins_r = ['(0, 200]', '(200, 400]', '(400, 600]', '(600, 800]',
       '(800, 1000]', '(1000, 1200]', '(1200, 1400]', '(1400, 1600]',
       '(1600, 1800]', '(1800, 2000]']
names_r = ['0-200', '201-400', '401-600', '601-800', '801-1000', '1001-1200', '1201-1400', '1401-1600', '1601-1800', '1801-2000']


dic=dict(zip(bins_r,names_r))
combined_df_r["size_m_f"]=combined_df_r["size_m_f"].replace(dic)

In [127]:
combined_df_r= combined_df_r[combined_df_r["size_m_f"] != 'nan']

In [128]:
combined_df_r["size_m_f"].unique()

array(['0-200', '201-400', '401-600', '601-800', '801-1000', '1001-1200',
       '1201-1400', '1401-1600', '1601-1800', '1801-2000'], dtype=object)

In [129]:
fig = px.scatter(combined_df_r, x="size_m", y="price",facet_col="size_m_f",color="size_m_f")
fig.update_xaxes(title="Size (m2)",range=[0,2000])
fig.update_yaxes(title="Price",range=[0,1000000])
fig.update_layout(title="Price vs Size (m2)")

fig.show()

## handle the bedrooms column and make the plot 

In [130]:
combined_df_r.info()

<class 'pandas.core.frame.DataFrame'>
Index: 26580 entries, 23897 to 13408
Data columns (total 17 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Property age    2 non-null      float64
 1   Bathrooms       26580 non-null  object 
 2   Bedrooms        26580 non-null  object 
 3   Property Type   26580 non-null  object 
 4   Available from  34 non-null     object 
 5   Property Size   26580 non-null  object 
 6   compound        26580 non-null  object 
 7   dev             26580 non-null  object 
 8   latitude        26580 non-null  int64  
 9   longitude       26580 non-null  int64  
 10  description     26580 non-null  object 
 11  url             26580 non-null  object 
 12  price           26580 non-null  float64
 13  Region          26580 non-null  object 
 14  spec_Compound   26580 non-null  object 
 15  size_m          26580 non-null  float64
 16  size_m_f        26580 non-null  object 
dtypes: float64(3), int64(2), object(

In [131]:
combined_df_r['Bedrooms']=combined_df_r['Bedrooms'].astype(str).str.strip()
combined_df_r['Bedrooms'].value_counts()

Bedrooms
3.0          8786
2.0          5630
4.0          3472
3            2403
5.0          1587
2            1367
4             895
6.0           704
1.0           640
5             427
7.0           214
1             173
6             154
8.0            67
7              37
8              16
3  + Maid       3
4  + Maid       3
2  + Maid       2
Name: count, dtype: int64

In [132]:
try_this=combined_df_r[combined_df_r["Bedrooms"].str.contains("Maid")]["Bedrooms"].str.replace('  + Maid','').str.replace('+','')
try_this=try_this[try_this!='studio']
try_this=try_this.astype(float) + 1
combined_df_r.loc[try_this.index,"Bedrooms"]=try_this

In [133]:
combined_df_r['Bedrooms'] = combined_df_r['Bedrooms'].astype(float)

In [134]:
property_types = ["Apartment", "Chalet", "Duplex", "Penthouse", "Townhouse", "Twin House", "Villa", "iVilla"]

top_property_types=combined_df_r['Property Type'].value_counts().head(8).index

filered_df=combined_df_r[combined_df_r['Property Type'].isin(top_property_types)]
  # Create the pivot table
pivot_df = pd.pivot_table(filered_df, values='price', index=['Bedrooms', 'Property Type'], aggfunc='median')

pivot_df = pivot_df.reset_index()


fig = px.bar(pivot_df, x='Bedrooms', y='price', facet_col='Property Type',width=1500,color='Property Type')


fig.update_layout(barmode='group',
                    title='Median Price by Bedrooms and property type',
                    xaxis_title='Bedrooms', yaxis_title='Median Price',
                    template='plotly_white',
                    height=400,
                    width=1100)
for i, facet_title in enumerate(property_types):
    fig.layout.annotations[i]['text'] = facet_title

fig.show()

In [ ]:
combined_df.to_csv('combined_df.csv', index=False)
copy2_df.to_csv('copy2_df.csv',index=False)
map_df.to_csv('map_df.csv',index=False)
size_df.to_csv('size_df.csv',index=False)
combined_df_r.to_csv('combined_df_r.csv',index=False)
down_pay_df.to_csv('down_pay_df.csv',index=False)